In [0]:
silver_path = "/Volumes/workspace/default/streaming_checkpoint/nyc_yellow_taxi_trip_records_from_Jan_to_Aug_2023.csv"

df_raw = spark.read.format("csv").option("header", "true") \
    .option("inferSchema", "true") \
    .csv(silver_path)

# df_raw.printSchema()
# df_raw.count()

19493059

In [0]:
from pyspark.sql.functions import col,to_timestamp,current_timestamp,year,month,row_number
from pyspark.sql.window import Window

df_std = (df_raw
          .withColumn("pickup_ts", to_timestamp(col("tpep_pickup_datetime")))
          .withColumn("dropoff_ts", to_timestamp(col("tpep_dropoff_datetime")))
          .withColumn("pickup_year", year(col("pickup_ts")))
          .withColumn("pickup_month", month(col("pickup_ts")))
          .withColumn("Vendor_id", col("VendorID").cast("integer"))
          .withColumn("pulocation_id",col("PULocationID").cast("int"))
          .withColumn("dolocation_id",col("DOLocationID").cast("int"))
          .withColumn("ingestion_ts", current_timestamp())
          .withColumnRenamed("_c0","id")
)

# df_std.show(5)
          
df_std.select("pickup_ts").count()
df_std.select("pickup_year", "pickup_month").distinct().orderBy(
    "pickup_year", "pickup_month"
).show()


+-----------+------------+
|pickup_year|pickup_month|
+-----------+------------+
|       2023|           1|
|       2023|           2|
|       2023|           3|
|       2023|           4|
|       2023|           5|
|       2023|           6|
+-----------+------------+



In [0]:
# batch_year = 2023
# batch_month = 6

# dbutils.widgets.removeAll()

dbutils.widgets.text("batch_year", "2023")
dbutils.widgets.text("batch_month", "7")
batch_year = int(dbutils.widgets.get("batch_year"))
batch_month = int(dbutils.widgets.get("batch_month"))

df_batch = (df_std
            .filter((col("pickup_year") == batch_year) & (col("pickup_month") == batch_month))
)
display(df_batch)
df_batch.count()
# df_std.select("pickup_year", "pickup_month") \
#       .distinct() \
#       .orderBy("pickup_year", "pickup_month") \
#       .show()


id VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge Airport_fee19 airport_fee20 pickup_ts dropoff_ts pickup_year pickup_month Vendor_id pulocation_id dolocation_id ingestion_ts 0 2 2023-06-30T23:59:59.000Z 2023-07-01T00:47:49.000Z 2.0 17.62 2.0 N 132 230 1 70.0 0.0 0.5 0.0 6.55 1.0 82.3 2.5 1.75 null 2023-06-30T23:59:59.000Z 2023-07-01T00:47:49.000Z 2023 6 2 132 230 2026-01-07T09:32:50.983Z 1 2 2023-06-30T23:59:57.000Z 2023-07-01T00:17:36.000Z 1.0 3.32 1.0 N 255 198 1 18.4 1.0 0.5 2.5 0.0 1.0 23.4 0.0 0.0 null 2023-06-30T23:59:57.000Z 2023-07-01T00:17:36.000Z 2023 6 2 255 198 2026-01-07T09:32:50.983Z 2 1 2023-06-30T23:59:55.000Z 2023-07-01T00:14:20.000Z 1.0 2.8 1.0 N 231 107 1 14.9 3.5 0.5 3.95 0.0 1.0 23.85 2.5 0.0 null 2023-06-30T23:59:55.000Z 2023-07-01T00:14:20.000Z 2023 6 1 231 107 2026-01-07T09:32:50.983Z 3 2 2023-06-30T23:59:55.000Z 2023-07-01T00:05:52.000Z 1.0 0.89 1.0 N 237 163 1 7.2 1.0 0.5 2.0 0.0 1.0 14.2 2.5 0.0 null 2023-06-30T23:59:55.000Z 2023-07-01T00:05:52.000Z 2023 6 2 237 163 2026-01-07T09:32:50.983Z 4 2 2023-06-30T23:59:55.000Z 2023-07-01T00:07:08.000Z 4.0 1.56 1.0 N 211 90 1 10.0 1.0 0.5 3.0 0.0 1.0 18.0 2.5 0.0 null 2023-06-30T23:59:55.000Z 2023-07-01T00:07:08.000Z 2023 6 2 211 90 2026-01-07T09:32:50.983Z 5 2 2023-06-30T23:59:54.000Z 2023-07-01T00:14:58.000Z 1.0 3.85 1.0 N 161 166 1 19.1 1.0 0.5 10.0 0.0 1.0 34.1 2.5 0.0 null 2023-06-30T23:59:54.000Z 2023-07-01T00:14:58.000Z 2023 6 2 161 166 2026-01-07T09:32:50.983Z 6 2 2023-06-30T23:59:53.000Z 2023-07-01T00:05:52.000Z 2.0 1.05 1.0 N 65 33 1 7.9 1.0 0.5 2.08 0.0 1.0 12.48 0.0 0.0 null 2023-06-30T23:59:53.000Z 2023-07-01T00:05:52.000Z 2023 6 2 65 33 2026-01-07T09:32:50.983Z 7 2 2023-06-30T23:59:53.000Z 2023-07-01T00:08:36.000Z 1.0 1.5 1.0 N 107 249 1 10.7 1.0 0.5 3.14 0.0 1.0 18.84 2.5 0.0 null 2023-06-30T23:59:53.000Z 2023-07-01T00:08:36.000Z 2023 6 2 107 249 2026-01-07T09:32:50.983Z 8 1 2023-06-30T23:59:52.000Z 2023-07-01T00:15:15.000Z 3.0 2.8 1.0 N 48 79 1 14.9 3.5 0.5 4.0 0.0 1.0 23.9 2.5 0.0 null 2023-06-30T23:59:52.000Z 2023-07-01T00:15:15.000Z 2023 6 1 48 79 2026-01-07T09:32:50.983Z 9 2 2023-06-30T23:59:51.000Z 2023-07-01T00:08:49.000Z 1.0 2.17 1.0 N 90 48 4 12.1 1.0 0.5 0.0 0.0 1.0 17.1 2.5 0.0 null 2023-06-30T23:59:51.000Z 2023-07-01T00:08:49.000Z 2023 6 2 90 48 2026-01-07T09:32:50.983Z 10 2 2023-06-30T23:59:51.000Z 2023-07-01T00:26:37.000Z null 10.16 null null 25 75 0 37.15 0.0 0.5 0.0 0.0 1.0 41.15 null null null 2023-06-30T23:59:51.000Z 2023-07-01T00:26:37.000Z 2023 6 2 25 75 2026-01-07T09:32:50.983Z 11 1 2023-06-30T23:59:50.000Z 2023-07-01T00:03:12.000Z 2.0 0.6 1.0 N 107 79 1 5.8 3.5 0.5 2.15 0.0 1.0 12.95 2.5 0.0 null 2023-06-30T23:59:50.000Z 2023-07-01T00:03:12.000Z 2023 6 1 107 79 2026-01-07T09:32:50.983Z 12 1 2023-06-30T23:59:50.000Z 2023-07-01T00:03:27.000Z 2.0 1.5 1.0 N 263 229 1 7.9 3.5 0.5 2.0 0.0 1.0 14.9 2.5 0.0 null 2023-06-30T23:59:50.000Z 2023-07-01T00:03:27.000Z 2023 6 1 263 229 2026-01-07T09:32:50.983Z 13 2 2023-06-30T23:59:49.000Z 2023-07-01T00:24:27.000Z 2.0 10.76 1.0 N 138 230 1 44.3 6.0 0.5 12.17 6.55 1.0 74.77 2.5 1.75 null 2023-06-30T23:59:49.000Z 2023-07-01T00:24:27.000Z 2023 6 2 138 230 2026-01-07T09:32:50.983Z 14 1 2023-06-30T23:59:49.000Z 2023-07-01T00:06:23.000Z 2.0 0.9 1.0 N 209 232 2 7.2 3.5 0.5 0.0 0.0 1.0 12.2 2.5 0.0 null 2023-06-30T23:59:49.000Z 2023-07-01T00:06:23.000Z 2023 6 1 209 232 2026-01-07T09:32:50.983Z 15 1 2023-06-30T23:59:47.000Z 2023-07-01T00:20:05.000Z 1.0 4.3 1.0 N 163 260 1 21.2 3.5 0.5 7.85 0.0 1.0 34.05 2.5 0.0 null 2023-06-30T23:59:47.000Z 2023-07-01T00:20:05.000Z 2023 6 1 163 260 2026-01-07T09:32:50.983Z 16 2 2023-06-30T23:59:47.000Z 2023-07-01T00:16:06.000Z 1.0 8.4 1.0 N 138 262 2 33.1 6.0 0.5 0.0 6.55 1.0 51.4 2.5 1.75 null 2023-06-30T23:59:47.000Z 2023-07-01T00:16:06.000Z 2023 6 2 138 

3307139

In [0]:
%sql
CREATE VOLUME IF NOT EXISTS workspace.default.data;
-- SHOW VOLUMES IN workspace.default;



In [0]:
if df_batch.count() == 0:
  raise Exception(f"No data to process for {batch_year}-{batch_month}")


In [0]:
from pyspark.sql.window import Window
dedup = Window.partitionBy(
    "VendorID",
    "PULocationID",
    "DOLocationID"
).orderBy(col("pickup_ts").desc())

df_dedup = df_batch.withColumn("row_number", row_number().over(dedup)) \
        .filter(col("row_number") == 1).drop("row_number")


SILVER_PATH = "/Volumes/workspace/default/data/silver/silver_taxi"

CHECKPOINT_PATH = "/Volumes/workspace/default/checkpoints/silver_taxi"


df_dedup.write.format("delta").mode("append").partitionBy("pickup_year","pickup_month").save(SILVER_PATH)
df_dedup.write \
  .format("delta") \
  .mode("overwrite") \
  .partitionBy("pickup_year", "pickup_month") \
  .save(SILVER_PATH)



In [0]:
# df_dedup.count()
spark.read.format("delta").load(SILVER_PATH).count()

In [0]:
%sql
DESCRIBE DETAIL delta.`/Volumes/workspace/default/data/silver/silver_taxi`;

DESCRIBE HISTORY delta.`/Volumes/workspace/default/data/silver/silver_taxi`;



In [0]:
%sql
OPTIMIZE delta.`/Volumes/workspace/default/data/silver/silver_taxi`
ZORDER BY (VendorID, PULocationID, DOLocationID);


In [0]:
#gold layer
from pyspark.sql.functions import col, sum, count

df_gold = spark.read.format("delta").load("/Volumes/workspace/default/data/silver/silver_taxi") \
    .groupBy("pickup_year", "pickup_month","PULocationID") \
    .agg(
        sum("total_amount").alias("total_revenue"),
        count("*").alias("total_trips")
    )
# df_gold.show(5)
# df_gold.count()

GOLD_PATH = "/Volumes/workspace/default/data/gold/gold_taxi"

df_gold.write \
    .mode("overwrite") \
    .format("delta") \
    .save(GOLD_PATH)

In [0]:
# spark.read.format("delta").load(GOLD_PATH).count()
df_gold.createOrReplaceTempView("gold_taxi")


In [0]:
%sql
MERGE INTO delta.`/Volumes/workspace/default/data/gold/gold_taxi` t
USING gold_taxi s
ON t.pickup_year = s.pickup_year AND t.PUlocationID = s.PUlocationID AND t.pickup_month = s.pickup_month
WHEN MATCHED THEN UPDATE SET *
WHEN NOT MATCHED THEN INSERT *

In [0]:
spark.read.format("delta").load("/Volumes/workspace/default/data/gold/gold_taxi").count()

In [0]:
%sql
DESCRIBE HISTORY delta.`/Volumes/workspace/default/data/gold/gold_taxi`;
    


In [0]:
%sql
OPTIMIZE delta.`/Volumes/workspace/default/data/gold/gold_taxi`
ZORDER BY (pickup_year, PUlocationID, pickup_month);

In [0]:
%sql
CREATE TABLE IF NOT EXISTS workspace.default.gold_taxi
AS
SELECT *
FROM delta.`/Volumes/workspace/default/data/gold/gold_taxi`;
    
DESCRIBE TABLE workspace.default.gold_taxi;


col_name data_type comment pickup_year int null pickup_month int null PULocationID int null total_revenue double null total_trips bigint null